In [ ]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

## Install libraries

In [2]:
! pip install plotly
! pip install talib-binary
! pip install keras_tuner

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 13.9 MB/s eta 0:00:0000:0100:01


## Import Libraries

In [3]:
import os
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import numpy as np
from sklearn.preprocessing import MinMaxScaler
import talib
from talib.abstract import *
from sklearn import metrics
import matplotlib.pyplot as plt

In [4]:
# read csv files
dataset_15Minutes = pd.read_csv("/kaggle/input/eurusd/dataset_per_15minutes.csv")
dataset_30Minutes = pd.read_csv("/kaggle/input/eurusd/dataset_per_30minutes.csv")
dataset_1Hour = pd.read_csv("/kaggle/input/eurusd/dataset_per_1hour.csv")
dataset_4Hours = pd.read_csv("/kaggle/input/eurusd/dataset_per_4hours.csv")

In [5]:
def prepare_data(dataset):
  """
  prepare_data removes converts variables to float and removes unused variables
  
  :param dataset : dataset
  :return : converted dataset
  """
  
  dataset['full_date'] = dataset['date_o'].astype('str') + ' ' + dataset['time_o'].astype('str')
  dataset['Date'] = pd.to_datetime(dataset['full_date'], format="%Y-%m-%d %H:%M:%S")
  dataset.drop(['date_o', 'time_o', 'full_date'], axis=1, inplace=True)
  dataset.drop_duplicates(keep=False, inplace=True)
  dataset.sort_values(by='Date', inplace=True)
  dataset.set_index(dataset['Date'], inplace=True)
  #dataset.drop(columns=['Unnamed: 0', 'tick_volume', 'spread', 'real_volume', 'Date'], inplace=True)
  dataset.drop(columns=['Unnamed: 0', 'tick_volume', 'real_volume', 'spread', 'Date'], inplace=True)
  dataset['open'] = dataset['open'].astype(float)
  dataset['high'] = dataset['high'].astype(float)
  dataset['low'] = dataset['low'].astype(float)
  dataset['close'] = dataset['close'].astype(float)
  
  return dataset

In [6]:
dataset_per_15Minutes = prepare_data(dataset_15Minutes)
dataset_per_30Minutes = prepare_data(dataset_30Minutes)
dataset_per_1Hour = prepare_data(dataset_1Hour)
dataset_per_4Hours = prepare_data(dataset_4Hours)

In [7]:
dataset_per_30Minutes.head()

open     high      low    close
Date                                                   
2020-12-31 23:00:00  1.22156  1.22156  1.22155  1.22155
2021-01-04 00:00:00  1.22395  1.22396  1.22280  1.22372
2021-01-04 00:30:00  1.22365  1.22398  1.22327  1.22341
2021-01-04 01:00:00  1.22336  1.22424  1.22304  1.22399
2021-01-04 01:30:00  1.22397  1.22528  1.22395  1.22501

In [8]:
dataset_per_30Minutes.describe()

open          high           low         close
count  22062.000000  22062.000000  22062.000000  22062.000000
mean       1.130297      1.130802      1.129783      1.130289
std        0.071751      0.071630      0.071868      0.071755
min        0.953920      0.955440      0.953570      0.953910
25%        1.072805      1.073350      1.072230      1.072802
50%        1.143450      1.143975      1.142905      1.143415
75%        1.188308      1.188757      1.187870      1.188308
max        1.234690      1.234940      1.233590      1.234690

In [9]:
fig = go.Figure(data=[go.Candlestick(x=dataset_per_30Minutes.index,
                open=dataset_per_30Minutes['open'],
                high=dataset_per_30Minutes['high'],
                low=dataset_per_30Minutes['low'],
                close=dataset_per_30Minutes['close'])],
                layout = {"xaxis": {"title": "date"}, "yaxis": {"title": "close"}, "title": "EUR/USD"}
                )

# hide weekends
fig.update_xaxes(
    rangebreaks=[
        dict(bounds=["sat", "mon"])
    ]
)

# remove Rangeslider
fig.update_layout(xaxis_rangeslider_visible=False)

fig.show()

In [10]:
f1 = go.Figure(
    data = [
        go.Scatter(x=dataset_per_30Minutes.index, y=dataset_per_30Minutes['close'], name="dataset"),
    ],
    layout = {"xaxis": {"title": "date"}, "yaxis": {"title": "close"}, "title": "EUR/USD"}
)
# hide weekends
f1.update_xaxes(
    rangebreaks=[
        dict(bounds=["sat", "mon"])
    ]
)
f1

In [11]:
def get_technical_inidcators(dataset):
  """
  add technical indicators as variables
  
  :param dataset : original dataset
  :return : original dataset with technical indicators 
  """
  # create 20, 30 and 200 Moving Average
  dataset['3_SMA'] = dataset['close'].rolling(window = 3).mean()
  dataset['7_SMA'] = dataset['close'].rolling(window = 7).mean()
  dataset['13_SMA'] = dataset['close'].rolling(window = 13).mean()

  # create ADX
  dataset['ADX_'] = talib.ADX(dataset['high'], dataset['low'], dataset['close'], timeperiod=14)

  # create WILLR
  dataset['WILLR_'] = talib.WILLR(dataset['high'], dataset['low'], dataset['close'], timeperiod=14)

  # create CCI
  dataset['CCI_'] = talib.CCI(dataset['high'], dataset['low'], dataset['close'], timeperiod=14)
  
  # create RSI
  dataset['RSI_'] = talib.RSI(dataset['close'], timeperiod=14)
  
  # create ATR
  dataset['ATR_'] = talib.ATR(dataset['high'], dataset['low'], dataset['close'], timeperiod=14)
  
  # create macd
  dataset['macd'], dataset['macdsignal'], dataset['macdhist'] = talib.MACD(dataset['close'], fastperiod=12, slowperiod=26, signalperiod=9)

  # create Bollinger Bands
  dataset['20sd'] = dataset['close'].rolling(window = 20).std()
  dataset['upper_band'] = dataset['3_SMA'] + (dataset['20sd']*2)
  dataset['lower_band'] = dataset['3_SMA'] - (dataset['20sd']*2)

  # Create Exponential moving average
  dataset['ema'] = dataset['close'].ewm(com=0.5).mean()

  # Create Momentum
  #dataset['momentum'] = dataset['close']-1
  #dataset['log_momentum'] = np.log(dataset['momentum'])

  return dataset

In [12]:
dataset_30mins = get_technical_inidcators(dataset_per_30Minutes)

In [13]:
dataset_30mins.head()

open     high      low    close     3_SMA  7_SMA  \
Date                                                                       
2020-12-31 23:00:00  1.22156  1.22156  1.22155  1.22155       NaN    NaN   
2021-01-04 00:00:00  1.22395  1.22396  1.22280  1.22372       NaN    NaN   
2021-01-04 00:30:00  1.22365  1.22398  1.22327  1.22341  1.222893    NaN   
2021-01-04 01:00:00  1.22336  1.22424  1.22304  1.22399  1.223707    NaN   
2021-01-04 01:30:00  1.22397  1.22528  1.22395  1.22501  1.224137    NaN   

                     13_SMA  ADX_  WILLR_  CCI_  RSI_  ATR_  macd  macdsignal  \
Date                                                                            
2020-12-31 23:00:00     NaN   NaN     NaN   NaN   NaN   NaN   NaN         NaN   
2021-01-04 00:00:00     NaN   NaN     NaN   NaN   NaN   NaN   NaN         NaN   
2021-01-04 00:30:00     NaN   NaN     NaN   NaN   NaN   NaN   NaN         NaN   
2021-01-04 01:00:00     NaN   NaN     NaN   NaN   NaN   NaN   NaN         NaN   
2021-01-04 01:30:00     NaN   NaN     NaN   NaN   NaN   NaN   NaN         NaN   

                     macdhist  20sd  upper_band  lower_band       ema  
Date                                                                   
2020-12-31 23:00:00       NaN   NaN         NaN         NaN  1.221550  
2021-01-04 00:00:00       NaN   NaN         NaN         NaN  1.223177  
2021-01-04 00:30:00       NaN   NaN         NaN         NaN  1.223338  
2021-01-04 01:00:00       NaN   NaN         NaN         NaN  1.223778  
2021-01-04 01:30:00       NaN   NaN         NaN         NaN  1.224603

In [14]:
dataset_30mins['target'] = dataset_30mins['close'].shift(-1)

In [15]:
dataset_30mins = dataset_30mins.dropna()

In [16]:
dataset_30mins.head()

open     high      low    close     3_SMA     7_SMA  \
Date                                                                          
2021-01-04 16:00:00  1.22990  1.23098  1.22936  1.23065  1.229800  1.229811   
2021-01-04 16:30:00  1.23065  1.23079  1.22836  1.22892  1.229817  1.229696   
2021-01-04 17:00:00  1.22892  1.22908  1.22712  1.22712  1.228897  1.229383   
2021-01-04 17:30:00  1.22712  1.22737  1.22605  1.22719  1.227743  1.228993   
2021-01-04 18:00:00  1.22715  1.22775  1.22666  1.22674  1.227017  1.228481   

                       13_SMA       ADX_      WILLR_        CCI_       RSI_  \
Date                                                                          
2021-01-04 16:00:00  1.229329  65.498481   -6.191370  101.132776  71.128138   
2021-01-04 16:30:00  1.229458  62.776648  -43.006263   12.608008  59.045651   
2021-01-04 17:00:00  1.229382  58.682849 -100.000000 -219.327894  49.604096   
2021-01-04 17:30:00  1.229212  55.139829  -76.876268 -267.572097  49.939341   
2021-01-04 18:00:00  1.229013  51.459524  -86.004057 -170.649432  47.740697   

                         ATR_      macd  macdsignal  macdhist      20sd  \
Date                                                                      
2021-01-04 16:00:00  0.001225  0.001541    0.001459  0.000082  0.002095   
2021-01-04 16:30:00  0.001311  0.001417    0.001451 -0.000034  0.001974   
2021-01-04 17:00:00  0.001357  0.001161    0.001393 -0.000232  0.001793   
2021-01-04 17:30:00  0.001355  0.000952    0.001304 -0.000353  0.001691   
2021-01-04 18:00:00  0.001336  0.000742    0.001192 -0.000450  0.001489   

                     upper_band  lower_band       ema   target  
Date                                                            
2021-01-04 16:00:00    1.233989    1.225611  1.230328  1.22892  
2021-01-04 16:30:00    1.233765    1.225869  1.229389  1.22712  
2021-01-04 17:00:00    1.232482    1.225311  1.227876  1.22719  
2021-01-04 17:30:00    1.231125    1.224361  1.227419  1.22674  
2021-01-04 18:00:00    1.229994    1.224039  1.226966  1.22535

In [17]:
f1 = go.Figure(
    data = [
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['close'], name="close"),
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['3_SMA'], name="20 simple moving average"),
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['7_SMA'], name="30 simple moving average"),
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['13_SMA'], name="200 simple moving average"),
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['upper_band'], name="upper band", fill=None, mode='lines', line_color='green',),
        go.Scatter(x=dataset_30mins.index, y=dataset_30mins['lower_band'], name="lower band", fill='tonexty', mode='lines', line_color='green'),
    ],
    layout = {"xaxis": {"title": "date"}, "yaxis": {"title": "close"}, "title": "EUR/USD"}
)

# hide weekends
f1.update_xaxes(
    rangebreaks=[
        dict(bounds=["sat", "mon"])
    ]
)

f1

In [18]:
columns = ['open', 'low', 'high']
dataset_30mins.drop(columns, inplace=True, axis=1)

/opt/conda/lib/python3.7/site-packages/pandas/core/frame.py:4913: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Modeling

In [19]:
import tensorflow as tf
from tensorflow.keras.layers import LSTM, Dense, Dropout, Bidirectional, Activation
from sklearn.model_selection import TimeSeriesSplit
from sklearn.metrics import mean_squared_error, r2_score
import matplotlib. dates as mandates
from sklearn. preprocessing import MinMaxScaler,StandardScaler
from sklearn import linear_model
from tensorflow.keras.models import Sequential, load_model
import tensorflow.keras.backend as K
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.utils import plot_model
import keras_tuner as kt
from sklearn.model_selection import train_test_split
from keras.preprocessing.sequence import TimeseriesGenerator

In [20]:
def timeseries_evaluation_metrics_func(y_true, y_pred):
     def mean_absolute_percentage_error(y_true, y_pred): 
         y_true, y_pred = np.array(y_true), np.array(y_pred)
         return np.mean(np.abs((y_true - y_pred) / y_true)) * 100
     print('Evaluation metric results:-')
     print(f'MSE is : {metrics.mean_squared_error(y_true, y_pred)}')
     print(f'MAE is : {metrics.mean_absolute_error(y_true, y_pred)}')
     print(f'RMSE is : {np.sqrt(metrics.mean_squared_error(y_true, y_pred))}')
     print(f'MAPE is : {mean_absolute_percentage_error(y_true, y_pred)}')
     print(f'R2 is : {metrics.r2_score(y_true, y_pred)}',end='\n\n')

In [21]:
scaler = MinMaxScaler()
scaled_data = scaler.fit_transform(dataset_30mins[['close','3_SMA', '7_SMA', '13_SMA', 'ADX_', 'WILLR_', 'CCI_', 'RSI_', 'ATR_', 'macd', 'macdsignal', 'macdhist', '20sd', 'upper_band', 'lower_band', 'ema']])


scaler_y = MinMaxScaler()
scaled_data_y = scaler_y.fit_transform(dataset_30mins[["target"]])

In [22]:
xtrain,xtest,ytrain,ytest=train_test_split(scaled_data,scaled_data_y,test_size=0.25,random_state=123,shuffle=False)

In [23]:
print(xtrain.shape)
print(xtest.shape)
print(ytrain.shape)
print(ytest.shape)

(16521, 16)
(5507, 16)
(16521, 1)
(5507, 1)


In [24]:
win_length=10
batch_size=32
num_features=16
train_generator = TimeseriesGenerator(xtrain, ytrain, length=win_length, batch_size=batch_size)
test_generator = TimeseriesGenerator(xtest, ytest, length=win_length, batch_size=batch_size)

## **vanilla LSTM**

In [40]:
model = Sequential()
model.add(LSTM(32, input_shape=(win_length,num_features), activation='sigmoid', return_sequences=False))
model.add(Dense(1))

2022-12-06 13:37:50.077097: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-12-06 13:37:50.078047: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-12-06 13:37:50.086708: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-12-06 13:37:50.087500: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from SysFS had negative value (-1), but there must be at least one NUMA node, so returning NUMA node zero
2022-12-06 13:37:50.088201: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:937] successful NUMA node read from S

In [41]:
model.compile(optimizer='adam', loss='mse', metrics=['mse', 'mae'])

In [42]:
history = model.fit(train_generator, validation_data=test_generator, epochs=100, verbose=1, shuffle =False)

2022-12-06 13:38:10.203723: I tensorflow/compiler/mlir/mlir_graph_optimization_pass.cc:185] None of the MLIR Optimization Passes are enabled (registered 2)


Epoch 1/100
516/516 [==============================] - 17s 26ms/step - loss: 0.0242 - mse: 0.0242 - mae: 0.0516 - val_loss: 0.0191 - val_mse: 0.0191 - val_mae: 0.1154
Epoch 2/100
516/516 [==============================] - 12s 24ms/step - loss: 0.0029 - mse: 0.0029 - mae: 0.0252 - val_loss: 0.0158 - val_mse: 0.0158 - val_mae: 0.1051
Epoch 3/100
516/516 [==============================] - 12s 24ms/step - loss: 0.0024 - mse: 0.0024 - mae: 0.0233 - val_loss: 0.0126 - val_mse: 0.0126 - val_mae: 0.0940
Epoch 4/100
516/516 [==============================] - 12s 22ms/step - loss: 0.0020 - mse: 0.0020 - mae: 0.0218 - val_loss: 0.0099 - val_mse: 0.0099 - val_mae: 0.0830
Epoch 5/100
516/516 [==============================] - 16s 31ms/step - loss: 0.0016 - mse: 0.0016 - mae: 0.0202 - val_loss: 0.0076 - val_mse: 0.0076 - val_mae: 0.0725
Epoch 6/100
516/516 [==============================] - 12s 22ms/step - loss: 0.0014 - mse: 0.0014 - mae: 0.0185 - val_loss: 0.0057 - val_mse: 0.0057 - val_mae: 0.062

In [43]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "loss"}, "title": "LSTM model loss"})

fig_loss.add_trace(go.Scatter(y=history.history["loss"],
                    mode='lines',
                    name='train loss'))
fig_loss.add_trace(go.Scatter(y=history.history["val_loss"],
                    mode='lines',
                    name='val loss'))
fig_loss

In [44]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "mse loss"}, "title": "LSTM model mse loss"})

fig_loss.add_trace(go.Scatter(y=history.history["mse"],
                    mode='lines',
                    name='train mse'))
fig_loss.add_trace(go.Scatter(y=history.history["val_mse"],
                    mode='lines',
                    name='val mse'))
fig_loss

In [45]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "mae loss"}, "title": "LSTM model mae loss"})

fig_loss.add_trace(go.Scatter(y=history.history["mae"],
                    mode='lines',
                    name='train mae'))
fig_loss.add_trace(go.Scatter(y=history.history["val_mae"],
                    mode='lines',
                    name='val mae'))
fig_loss

In [46]:
model.evaluate(test_generator)

172/172 [==============================] - 1s 3ms/step - loss: 1.4929e-04 - mse: 1.4929e-04 - mae: 0.0099


[0.00014928834571037441, 0.00014928834571037441, 0.009944276884198189]

In [47]:
predictions = model.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [48]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.0002470220731817897
MAE is : 0.012452108499089027
RMSE is : 0.015716935871275598
MAPE is : inf
R2 is : 0.9776750630876162



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## **Keras tuner:**

so, i used random search from KerasTuner

In [51]:
def model_builder(hp):
    model = Sequential()
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=False, input_shape= (win_length,num_features)))
    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse','mae'])
    
    return model

In [52]:
"""def model_builder(hp):
    model = Sequential()
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True, input_shape= (win_length,num_features)))
    for i in range(hp.Int('n_layers', 1, 4)):
        model.add(LSTM(hp.Int(f'lstm_{i}_units',min_value=32,max_value=512,step=32),return_sequences=True))
    model.add(LSTM(hp.Int('layer_2_neurons',min_value=32,max_value=512,step=32)))
    model.add(Dropout(hp.Float('Dropout_rate',min_value=0,max_value=0.5,step=0.1)))
    model.add(Dense(30, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
   
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model"""

"def model_builder(hp):\n    model = Sequential()\n    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True, input_shape= (win_length,num_features)))\n    for i in range(hp.Int('n_layers', 1, 4)):\n        model.add(LSTM(hp.Int(f'lstm_{i}_units',min_value=32,max_value=512,step=32),return_sequences=True))\n    model.add(LSTM(hp.Int('layer_2_neurons',min_value=32,max_value=512,step=32)))\n    model.add(Dropout(hp.Float('Dropout_rate',min_value=0,max_value=0.5,step=0.1)))\n    model.add(Dense(30, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))\n    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))\n   \n    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])\n    \n    return model"

In [53]:
tuner = kt.RandomSearch(model_builder, objective="mse", max_trials = 10, executions_per_trial =1,directory = "")

tuner.search(train_generator, epochs = 100, batch_size =80, validation_data=(test_generator))

Trial 10 Complete [00h 05m 00s]
mse: 0.5867653489112854

Best mse So Far: 1.5061188605614007e-05
Total elapsed time: 00h 50m 17s


In [54]:
best_model = tuner.get_best_models(num_models=1)[0]

In [55]:
tuner.results_summary()

Results summary
Results in ./untitled_project
Showing 10 best trials
Trial summary
Hyperparameters:
input_unit: 512
dense_activation: relu
Score: 1.5061188605614007e-05
Trial summary
Hyperparameters:
input_unit: 256
dense_activation: sigmoid
Score: 1.5223584341583773e-05
Trial summary
Hyperparameters:
input_unit: 448
dense_activation: relu
Score: 1.5880372302490287e-05
Trial summary
Hyperparameters:
input_unit: 288
dense_activation: relu
Score: 1.5971187167451717e-05
Trial summary
Hyperparameters:
input_unit: 320
dense_activation: sigmoid
Score: 1.6239735487033613e-05
Trial summary
Hyperparameters:
input_unit: 96
dense_activation: sigmoid
Score: 1.6264550140476786e-05
Trial summary
Hyperparameters:
input_unit: 512
dense_activation: sigmoid
Score: 1.632428575248923e-05
Trial summary
Hyperparameters:
input_unit: 448
dense_activation: sigmoid
Score: 1.654964580666274e-05
Trial summary
Hyperparameters:
input_unit: 224
dense_activation: sigmoid
Score: 1.6574282199144363e-05
Trial summary
Hy

In [56]:
best_model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm (LSTM)                  (None, 512)               1083392   
_________________________________________________________________
dense (Dense)                (None, 1)                 513       
Total params: 1,083,905
Trainable params: 1,083,905
Non-trainable params: 0
_________________________________________________________________


In [57]:
y_pred = best_model.predict(test_generator)

In [58]:
#Predicted vs Close Value – LSTM
df_predictions = pd.DataFrame(y_pred)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [59]:
df_test_last_n = df_test.iloc[:-10]

In [60]:
timeseries_evaluation_metrics_func(df_test_last_n[0], df_predictions[0])

Evaluation metric results:-
MSE is : 0.00010157643325036187
MAE is : 0.007172861336684941
RMSE is : 0.010078513444469967
MAPE is : inf
R2 is : 0.9908198994733947



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## **training a stacked Lstm model**

In [33]:
win_length=10
batch_size=64
num_features=16
train_generator = TimeseriesGenerator(xtrain, ytrain, length=win_length, batch_size=batch_size)
test_generator = TimeseriesGenerator(xtest, ytest, length=win_length, batch_size=batch_size)

In [35]:
#Building the LSTM Model
lstm_stacked = Sequential()
lstm_stacked.add(LSTM(64,return_sequences = True,activation='sigmoid', input_shape = (win_length,num_features)))
lstm_stacked.add(LSTM(32,return_sequences = True))
lstm_stacked.add(LSTM(32))
lstm_stacked.add(Dense(1))
lstm_stacked.compile(optimizer='adam', loss='mse', metrics=['mse', 'mae'])

history = lstm_stacked.fit(train_generator, validation_data=(test_generator), epochs=100,batch_size=64, verbose=1, shuffle =False)

Epoch 1/100
258/258 [==============================] - 11s 30ms/step - loss: 0.0162 - mse: 0.0162 - mae: 0.0660 - val_loss: 0.0347 - val_mse: 0.0347 - val_mae: 0.1564
Epoch 2/100
258/258 [==============================] - 8s 29ms/step - loss: 0.0089 - mse: 0.0089 - mae: 0.0547 - val_loss: 0.0486 - val_mse: 0.0486 - val_mae: 0.1943
Epoch 3/100
258/258 [==============================] - 8s 30ms/step - loss: 0.0081 - mse: 0.0081 - mae: 0.0504 - val_loss: 0.0481 - val_mse: 0.0481 - val_mae: 0.1923
Epoch 4/100
258/258 [==============================] - 7s 27ms/step - loss: 0.0081 - mse: 0.0081 - mae: 0.0498 - val_loss: 0.0457 - val_mse: 0.0457 - val_mae: 0.1864
Epoch 5/100
258/258 [==============================] - 8s 31ms/step - loss: 0.0081 - mse: 0.0081 - mae: 0.0502 - val_loss: 0.0479 - val_mse: 0.0479 - val_mae: 0.1917
Epoch 6/100
258/258 [==============================] - 7s 28ms/step - loss: 0.0104 - mse: 0.0104 - mae: 0.0600 - val_loss: 0.0497 - val_mse: 0.0497 - val_mae: 0.1966
Epo

In [36]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "loss"}, "title": "LSTM model loss"})

fig_loss.add_trace(go.Scatter(y=history.history["loss"],
                    mode='lines',
                    name='train loss'))
fig_loss.add_trace(go.Scatter(y=history.history["val_loss"],
                    mode='lines',
                    name='val loss'))
fig_loss

In [37]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "mae loss"}, "title": "LSTM model mae loss"})

fig_loss.add_trace(go.Scatter(y=history.history["mae"],
                    mode='lines',
                    name='train mae'))
fig_loss.add_trace(go.Scatter(y=history.history["val_mae"],
                    mode='lines',
                    name='val mae'))
fig_loss

In [38]:
lstm_stacked.evaluate(test_generator)

86/86 [==============================] - 0s 5ms/step - loss: 0.0035 - mse: 0.0035 - mae: 0.0438 


[0.0034520758781582117, 0.0034520758781582117, 0.04380970448255539]

In [39]:
y_pred = lstm_stacked.predict(test_generator)

In [40]:
#Predicted vs Close Value – LSTM
df_predictions = pd.DataFrame(y_pred)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [41]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.0034246740355830447
MAE is : 0.04381963345006384
RMSE is : 0.05852071458537605
MAPE is : inf
R2 is : 0.6904906885239985



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## stacked LSTM : random tuner

In [42]:
def model_builder(hp):
    model = Sequential()
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True, input_shape= (win_length,num_features)))
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True))
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32)))
    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid', 'gelu'],default='relu')))
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model

In [43]:
tuner1 = kt.RandomSearch(model_builder, objective="mse", max_trials = 10, executions_per_trial =1,directory = "/")

In [45]:
tuner1.search(train_generator, epochs = 100, batch_size =64, validation_data=(test_generator))

Trial 10 Complete [00h 05m 09s]
mse: 0.5867654085159302

Best mse So Far: 2.212350955232978e-05
Total elapsed time: 00h 52m 03s


In [46]:
best_model = tuner1.get_best_models(num_models=1)[0]

In [47]:
tuner1.results_summary()

Results summary
Results in /untitled_project
Showing 10 best trials
Trial summary
Hyperparameters:
input_unit: 384
dense_activation: sigmoid
Score: 2.212350955232978e-05
Trial summary
Hyperparameters:
input_unit: 448
dense_activation: gelu
Score: 2.2128833734313957e-05
Trial summary
Hyperparameters:
input_unit: 128
dense_activation: sigmoid
Score: 2.2591086235479452e-05
Trial summary
Hyperparameters:
input_unit: 288
dense_activation: gelu
Score: 2.2699410692439415e-05
Trial summary
Hyperparameters:
input_unit: 384
dense_activation: gelu
Score: 2.53062644333113e-05
Trial summary
Hyperparameters:
input_unit: 128
dense_activation: relu
Score: 2.8415712222340517e-05
Trial summary
Hyperparameters:
input_unit: 160
dense_activation: gelu
Score: 2.9611650461447425e-05
Trial summary
Hyperparameters:
input_unit: 224
dense_activation: sigmoid
Score: 2.9713633921346627e-05
Trial summary
Hyperparameters:
input_unit: 64
dense_activation: gelu
Score: 3.073583502555266e-05
Trial summary
Hyperparameter

In [48]:
y_pred = best_model.predict(test_generator)

In [49]:
#Predicted vs Close Value – LSTM
df_predictions = pd.DataFrame(y_pred)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [50]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.002337337081700472
MAE is : 0.032578272521548504
RMSE is : 0.04834601412423233
MAPE is : inf
R2 is : 0.7887601613094025



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## **Using BayesianOptimization Tuner**

In [45]:
tuner2 = kt.BayesianOptimization(model_builder, objective="mse", max_trials = 10, executions_per_trial =1,directory = "")

In [46]:
tuner2.search(train_generator, epochs = 100, batch_size =80, validation_data=(test_generator))

Trial 10 Complete [00h 08m 15s]
mse: 2.0556613890221342e-05

Best mse So Far: 1.923641684697941e-05
Total elapsed time: 01h 24m 08s


In [47]:
best_model = tuner2.get_best_models(num_models=1)[0]

In [48]:
tuner2.results_summary()

Results summary
Results in ./untitled_project
Showing 10 best trials
Trial summary
Hyperparameters:
input_unit: 96
dense_activation: sigmoid
Score: 1.923641684697941e-05
Trial summary
Hyperparameters:
input_unit: 160
dense_activation: sigmoid
Score: 1.9522822185535915e-05
Trial summary
Hyperparameters:
input_unit: 160
dense_activation: sigmoid
Score: 1.979517037398182e-05
Trial summary
Hyperparameters:
input_unit: 128
dense_activation: sigmoid
Score: 2.008742194448132e-05
Trial summary
Hyperparameters:
input_unit: 160
dense_activation: sigmoid
Score: 2.052203672064934e-05
Trial summary
Hyperparameters:
input_unit: 160
dense_activation: sigmoid
Score: 2.0556613890221342e-05
Trial summary
Hyperparameters:
input_unit: 96
dense_activation: relu
Score: 2.120283716067206e-05
Trial summary
Hyperparameters:
input_unit: 448
dense_activation: sigmoid
Score: 2.198161200794857e-05
Trial summary
Hyperparameters:
input_unit: 64
dense_activation: sigmoid
Score: 2.2450383767136373e-05
Trial summary
Hy

In [49]:
y_pred = best_model.predict(test_generator)

In [50]:
#Predicted vs Close Value – LSTM
df_predictions = pd.DataFrame(y_pred)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

## Adding more lstm layers and dropouts

In [51]:
#Building the LSTM Model
lstm_stacked = Sequential()
lstm_stacked.add(LSTM(64, input_shape=(win_length,num_features), activation='gelu', return_sequences=True))
lstm_stacked.add(Dropout(0.2))
lstm_stacked.add(LSTM(units = 64, return_sequences=True))
lstm_stacked.add(Dropout(0.2))
lstm_stacked.add(LSTM(units = 64, return_sequences=False))
lstm_stacked.add(Dropout(0.2))
lstm_stacked.add(Dense(1))

lstm_stacked.compile(optimizer='adam', loss='mse', metrics=['mse', 'mae'])

history = lstm_stacked.fit(train_generator, validation_data=(test_generator), epochs=100,batch_size=64, verbose=1, shuffle =False)

Epoch 1/100
258/258 [==============================] - 12s 33ms/step - loss: 0.0218 - mse: 0.0218 - mae: 0.0835 - val_loss: 0.0118 - val_mse: 0.0118 - val_mae: 0.0876
Epoch 2/100
258/258 [==============================] - 7s 29ms/step - loss: 0.0076 - mse: 0.0076 - mae: 0.0618 - val_loss: 0.0162 - val_mse: 0.0162 - val_mae: 0.1058
Epoch 3/100
258/258 [==============================] - 7s 28ms/step - loss: 0.0077 - mse: 0.0077 - mae: 0.0610 - val_loss: 0.0228 - val_mse: 0.0228 - val_mae: 0.1307
Epoch 4/100
258/258 [==============================] - 7s 29ms/step - loss: 0.0083 - mse: 0.0083 - mae: 0.0633 - val_loss: 0.0247 - val_mse: 0.0247 - val_mae: 0.1391
Epoch 5/100
258/258 [==============================] - 8s 29ms/step - loss: 0.0080 - mse: 0.0080 - mae: 0.0607 - val_loss: 0.0200 - val_mse: 0.0200 - val_mae: 0.1249
Epoch 6/100
258/258 [==============================] - 8s 30ms/step - loss: 0.0081 - mse: 0.0081 - mae: 0.0601 - val_loss: 0.0146 - val_mse: 0.0146 - val_mae: 0.1059
Epo

In [52]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "loss"}, "title": "LSTM model loss"})

fig_loss.add_trace(go.Scatter(y=history.history["loss"],
                    mode='lines',
                    name='train loss'))
fig_loss.add_trace(go.Scatter(y=history.history["val_loss"],
                    mode='lines',
                    name='val loss'))
fig_loss

In [53]:
fig_loss = go.Figure(layout = {"xaxis": {"title": "epoch"}, "yaxis": {"title": "mae loss"}, "title": "LSTM model mae loss"})

fig_loss.add_trace(go.Scatter(y=history.history["mae"],
                    mode='lines',
                    name='train mae'))
fig_loss.add_trace(go.Scatter(y=history.history["val_mae"],
                    mode='lines',
                    name='val mae'))
fig_loss

In [54]:
lstm_stacked.evaluate(test_generator)

86/86 [==============================] - 0s 5ms/step - loss: 0.0219 - mse: 0.0219 - mae: 0.1201


[0.021930085495114326, 0.021930085495114326, 0.1200559064745903]

In [55]:
predictions = lstm_stacked.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [56]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.021753709584782375
MAE is : 0.1193277372469297
RMSE is : 0.1474913881715891
MAPE is : inf
R2 is : -0.9660194242365643



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## random tuner on an stacked-LSTM model

In [57]:
def build_model(hp):
    activation = hp.Choice('activation', 
                        [
                          'relu',
                          'tanh',
                          'linear',
                          'gelu'
                        ])
    
    model = Sequential()
    model.add(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), activation=activation, return_sequences=True, input_shape= ( X_train.shape[1],X_train.shape[2])))
    for i in range(hp.Int('n_layers', 1, 4)):
        model.add(LSTM(hp.Int(f'lstm_{i}_units',min_value=32,max_value=512,step=32),return_sequences=True))
    model.add(LSTM(hp.Int('layer_2_neurons',min_value=32,max_value=512,step=32)))
    model.add(Dropout(hp.Float('Dropout_rate',min_value=0,max_value=0.5,step=0.1)))
    model.add(Dense(1, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
   
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model

In [58]:
tuner3 = kt.RandomSearch(model_builder, objective="mse", max_trials = 10, executions_per_trial =1,directory = "./t")

In [59]:
tuner3.search(train_generator, epochs = 100, batch_size =64, validation_data=(test_generator))

Trial 10 Complete [00h 04m 49s]
mse: 2.2739566702512093e-05

Best mse So Far: 2.082936953229364e-05
Total elapsed time: 00h 50m 09s


In [60]:
best_model = tuner3.get_best_models(num_models=1)[0]

In [61]:
predictions = best_model.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [62]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.023117153463874614
MAE is : 0.08092677489747031
RMSE is : 0.15204326181674285
MAPE is : inf
R2 is : -1.0892424147662783



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



## Bidirectional LSTM

In [61]:
model = Sequential()
model.add(Bidirectional(LSTM(64, activation='relu', input_shape=(win_length,num_features),return_sequences=True)))
model.add(Bidirectional(LSTM(32, activation='relu', return_sequences=True)))
model.add(Dropout(0.2))
model.add(Flatten())
model.add(Dense(64, activation='relu'))
model.add(Dense(8, activation='relu'))
model.add(Dense(1))

model.compile(optimizer='adam', loss='mse', metrics=['mse', 'mae'])

history = model.fit(train_generator, validation_data=(test_generator), epochs=100,batch_size=80, verbose=1, shuffle =False)

Epoch 1/100
516/516 [==============================] - 49s 88ms/step - loss: 0.0111 - mse: 0.0111 - mae: 0.0447 - val_loss: 0.0099 - val_mse: 0.0099 - val_mae: 0.0796
Epoch 2/100
516/516 [==============================] - 44s 85ms/step - loss: 0.0018 - mse: 0.0018 - mae: 0.0280 - val_loss: 0.0130 - val_mse: 0.0130 - val_mae: 0.0914
Epoch 3/100
516/516 [==============================] - 44s 84ms/step - loss: 0.0018 - mse: 0.0018 - mae: 0.0261 - val_loss: 0.0168 - val_mse: 0.0168 - val_mae: 0.1064
Epoch 4/100
516/516 [==============================] - 44s 86ms/step - loss: 0.0019 - mse: 0.0019 - mae: 0.0258 - val_loss: 0.0197 - val_mse: 0.0197 - val_mae: 0.1162
Epoch 5/100
516/516 [==============================] - 44s 85ms/step - loss: 0.0023 - mse: 0.0023 - mae: 0.0263 - val_loss: 0.0245 - val_mse: 0.0245 - val_mae: 0.1309
Epoch 6/100
516/516 [==============================] - 44s 85ms/step - loss: 0.0029 - mse: 0.0029 - mae: 0.0285 - val_loss: 0.0290 - val_mse: 0.0290 - val_mae: 0.142

In [62]:
predictions = model.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [63]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.007738103910665388
MAE is : 0.06989076514648283
RMSE is : 0.08796649311337464
MAPE is : inf
R2 is : 0.3006589273504239



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



In [65]:
modell = Sequential()
modell.add(Bidirectional(LSTM(64, activation='relu', input_shape=(win_length,num_features)))) #elu
modell.add(Dense(1))

modell.compile(optimizer='adam', loss='mse', metrics=['mse', 'mae'])

history = modell.fit(train_generator, validation_data=(test_generator), epochs=100,batch_size=40, verbose=1, shuffle =False)

Epoch 1/100
516/516 [==============================] - 24s 43ms/step - loss: 0.0075 - mse: 0.0075 - mae: 0.0231 - val_loss: 0.0016 - val_mse: 0.0016 - val_mae: 0.0320
Epoch 2/100
516/516 [==============================] - 22s 42ms/step - loss: 1.0994e-04 - mse: 1.0994e-04 - mae: 0.0062 - val_loss: 0.0013 - val_mse: 0.0013 - val_mae: 0.0279
Epoch 3/100
516/516 [==============================] - 21s 41ms/step - loss: 5.6337e-05 - mse: 5.6337e-05 - mae: 0.0050 - val_loss: 0.0013 - val_mse: 0.0013 - val_mae: 0.0279
Epoch 4/100
516/516 [==============================] - 22s 43ms/step - loss: 4.9634e-05 - mse: 4.9634e-05 - mae: 0.0050 - val_loss: 0.0013 - val_mse: 0.0013 - val_mae: 0.0275
Epoch 5/100
516/516 [==============================] - 22s 43ms/step - loss: 4.5505e-05 - mse: 4.5505e-05 - mae: 0.0049 - val_loss: 0.0016 - val_mse: 0.0016 - val_mae: 0.0297
Epoch 6/100
516/516 [==============================] - 22s 42ms/step - loss: 5.6937e-05 - mse: 5.6937e-05 - mae: 0.0053 - val_loss: 0

In [66]:
predictions = modell.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [67]:
timeseries_evaluation_metrics_func(df_test[0].iloc[:-10], df_predictions[0])

Evaluation metric results:-
MSE is : 0.0010794524644230567
MAE is : 0.0252884386408956
RMSE is : 0.03285502190568523
MAPE is : inf
R2 is : 0.9024430980691063



/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:4: RuntimeWarning:

divide by zero encountered in true_divide



In [63]:
def model_builder(hp):
    model = Sequential()
    model.add(Bidirectional(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), activation=hp.Choice('dense_activation',values=['relu', 'sigmoid', 'gelu'],default='relu'), input_shape= (win_length,num_features))))
    model.add(Dense(1))
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model

In [64]:
tuner5 = kt.RandomSearch(model_builder, objective="mse", max_trials = 10, executions_per_trial =1,directory = "./bidirectional_test")

In [65]:
tuner5.search(train_generator, epochs = 100, batch_size =240, validation_data=(test_generator))

Trial 10 Complete [00h 22m 14s]
mse: 2.747463804553263e-05

Best mse So Far: 1.3131761988915969e-05
Total elapsed time: 04h 12m 35s


In [66]:
best_model = tuner5.get_best_models(num_models=1)[0]

In [67]:
predictions = best_model.predict(test_generator)
df_predictions = pd.DataFrame(predictions)
df_test = pd.DataFrame(ytest)

fig = go.Figure(layout = {"xaxis": {"title": "time"}, "yaxis": {"title": "close"}, "title": "Prediction by LSTM"})

fig.add_trace(go.Scatter(y=df_predictions[0],
                    mode='lines',
                    name='predictions'))
fig.add_trace(go.Scatter(y=df_test[0],
                    mode='lines',
                    name='test'))

In [ ]:
"""def model_builder(hp):
    model = Sequential()
    model.add(Bidirectional(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True,activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu'), input_shape= (win_length,num_features))))
    model.add(Bidirectional(LSTM(hp.Int('input_unit',min_value=32,max_value=512,step=32), return_sequences=True,activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu'))))
    model.add(Dropout(0.2))
    model.add(Flatten())
    model.add(Dense(64, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
    model.add(Dense(8, activation=hp.Choice('dense_activation',values=['relu', 'sigmoid'],default='relu')))
    model.add(Dense(1))
    model.compile(loss='mean_squared_error', optimizer='adam',metrics = ['mse'])
    
    return model"""